# Pick particles with crYOLO

This example covers [crYOLO Tutorial 2](https://cryolo.readthedocs.io/en/stable/tutorials/tutorial_overview.html#tutorial-2-pick-particles-by-training-a-model-for-your-data), using particle picks from cryoSPARC as training data. The crYOLO GUI is not required for this tutorial.

This example ran in a conda environment with cryolo and cudatoolkit 11 installed with the following commands:

```sh
conda create -n cryolo -c conda-forge \
   python=3.8 \
   cudatoolkit=11.6 \
   cudnn=8.3 \
   libtiff \
   pyqt=5 \
   wxPython=4.1.1 \
   adwaita-icon-theme
conda activate cryolo
pip install -U pip
pip install nvidia-pyindex
pip install cryolo[c11] cryosparc-tools
```

## Prelude

Connect to a cryoSPARC instance with `cryosparc.tools.CryoSPARC` and get the project handle. This project contains a workspace `W3` with the following jobs:

* Patch CTF with 20 motion-corrected and CTF-estimated micrographs
* Exposures Sets tool that splits micrographs into 5 for training/validation and 15 for picking from the trained model
* Manual Picker that picks 5 training micrographs to completion

In [14]:
from cryosparc.tools import CryoSPARC

cs = CryoSPARC(host="cryoem5", port=61000)
assert cs.test_connection()

project = cs.find_project("P70")

Connection succeeded to cryoSPARC command_core at http://cryoem5:61002
Connection succeeded to cryoSPARC command_vis at http://cryoem5:61003


Programatically create and build a new external job. This job will contain the results of both training and picking for the remaining micrographs. 

Connect the training picks, training micrographs and remaining micrographs as inputs. Specify the `micrograph_blob` as slots for the micrographs to retrieve the motion-corrected blob location. Other micrograph slots will be connected as passthroughs. Specify the `location` slot for particles to load the micrograph path and $(x, y)$ coordinates for each particle.

Create an output slots for the resulting picks. It will only have a location slot.

In [19]:
job = project.create_external_job("W3", title="crYOLO Picks")
job.connect("J50", "split_0", "train_micrographs", slots=["micrograph_blob"])
job.connect("J57", "particles", "train_particles", slots=["location"])
job.connect("J50", "split_0", "all_micrographs", slots=["micrograph_blob"])
job.connect("J50", "remainder", "all_micrographs", slots=["micrograph_blob"])
job.add_output("particle", "predicted_particles", slots=["location", "pick_stats"])

'predicted_particles'

Start the job to write to the outputs and job log. This puts the job in "Waiting" status.

In [20]:
job.start()

## Data Preparation

Use the job directory as crYOLO's working directory. Create all the necessary subfolders there. Note that this way of accessing the job directory only works if this script runs on a system with access to the same project file system as cryoSPARC.

In [21]:
from pathlib import Path

project_folder = Path(project.dir())
job_folder = Path(job.dir())
full_data_folder = job_folder / "full_data"
train_image_folder = job_folder / "train_image"
train_annot_folder = job_folder / "train_annot"

full_data_folder.mkdir(exist_ok=True)
train_image_folder.mkdir(exist_ok=True)
train_annot_folder.mkdir(exist_ok=True)

Load the input micrographs and link them into the `full_data` and `train_image` directories. This results in the following directory structure:

```
/path/to/project/JX/
├── full_data
│   ├── mic01.mrc -> /path/to/project/JY/motioncorrected/mic01.mrc
│   ├── mic02.mrc -> /path/to/project/JY/motioncorrected/mic02.mrc
│   ├── ...
│   └── mic20.mrc -> /path/to/project/JY/motioncorrected/mic20.mrc
└── train_image
    ├── mic01.mrc -> /path/to/project/JY/motioncorrected/mic01.mrc
    ├── mic02.mrc -> /path/to/project/JY/motioncorrected/mic02.mrc
    ├── mic03.mrc -> /path/to/project/JY/motioncorrected/mic03.mrc
    ├── mic04.mrc -> /path/to/project/JY/motioncorrected/mic04.mrc
    └── mic05.mrc -> /path/to/project/JY/motioncorrected/mic05.mrc
```

In [22]:
all_micrographs = job.load_input("all_micrographs", ["micrograph_blob"])
train_micrographs = job.load_input("train_micrographs", ["micrograph_blob"])

for mic in all_micrographs.rows():
    source = project_folder / mic["micrograph_blob/path"]
    target = full_data_folder / source.name
    target.symlink_to(source)

for mic in train_micrographs.rows():
    source = project_folder / mic["micrograph_blob/path"]
    target = train_image_folder / source.name
    target.symlink_to(source)

crYOLO requires the particle locations for each micrograph in STAR format with the following directory stucture:

```
/path/to/project/JX/
└── train_annot
    └── STAR
        ├── mic01.star
        ├── mic02.star
        ├── mic03.star
        ├── mic04.star
        └── mic05.star

```

Load the training particle locations. Split them up my micrograph path. Compute the pixel locations and save them to a star file in this format.

In [23]:
import numpy as np
from numpy.core import records
from cryosparc import star

train_annot_star_folder = train_annot_folder / "STAR"
train_annot_star_folder.mkdir(exist_ok=True)

train_particles = job.load_input("train_particles", ["location"])

for micrograph_path, particles in train_particles.split_by("location/micrograph_path").items():
    micrograph_path = Path(micrograph_path)
    star_file_name = micrograph_path.stem + ".star"

    mic_w = particles["location/micrograph_shape"][:, 1]
    mic_h = particles["location/micrograph_shape"][:, 0]
    center_x = particles["location/center_x_frac"]
    center_y = particles["location/center_y_frac"]
    location_x = center_x * mic_w
    location_y = center_y * mic_h

    star.write(
        train_annot_star_folder / star_file_name,
        records.fromarrays([location_x, location_y], names=["rlnCoordinateX", "rlnCoordinateY"]),
    )

Preview of the particle locations used on the last training micrograph:

In [24]:
%matplotlib inline

from cryosparc import mrc
from cryosparc.util import downsample, lowpass
import matplotlib.pyplot as plt

header, mic = mrc.read(project_folder / micrograph_path)
binned = downsample(mic, factor=3)
lowpassed = lowpass(binned, psize_A=0.6575, cutoff_resolution_A=20, order=0.7)
height, width = lowpassed.shape
vmin = np.percentile(lowpassed, 1)
vmax = np.percentile(lowpassed, 99)

fig, ax = plt.subplots(figsize=(7.5, 8), dpi=144)
ax.axis("off")
ax.imshow(lowpassed, cmap="gray", vmin=vmin, vmax=vmax, origin="lower")
ax.scatter(center_x * width, center_y * height, c="yellow", marker="+")

fig.tight_layout()

## Configuration

Generate crYOLO's configuration file from the command line. On this machine, crYOLO is installed in a conda environment in the home directory. Run the `cryolo_gpu.py config` command from the job directory to generate a configuration file in the project directory. Use a box size of 130 for this dataset.

Use `job.subprocess` to forward the output to the job stream log. Arguments are similar to Python's `subprocess.Popen()`.

In [25]:
job.subprocess(
    [
        "cryolo_gui.py",
        "config",
        "config_cryolo.json",
        "130",
        "--train_image_folder",
        train_image_folder.name,
        "--train_annot_folder",
        train_annot_folder.name,
    ],
    cwd=job_folder,
)

#####################################################
Important debugging information.
In case of any problems, please provide this information.
#####################################################
/u/nfrasser/miniconda3/envs/tools/bin/cryolo_gui.py config config_cryolo.json 130
--train_image_folder train_image
--train_annot_folder train_annot
#####################################################

 Wrote config to config_cryolo.json


## Training

Run training on GPU 0 with 5 warmup-epochs and an early stop of 15.

The output of this command is quite long, so set `mute=True` to hide it (it will still appear in the job's stream log).

Use the `checkpoint_line_pattern` flag new training epoch lines as the beginning of a checkpoint in the stream log.

In [26]:
job.subprocess(
    ["cryolo_train.py", "-c", "config_cryolo.json", "-w", "5", "-g", "0", "-e", "15"],
    cwd=job_folder,
    mute=True,
    checkpoint=True,
    checkpoint_line_pattern=r"Epoch \d+/\d+",  # e.g., "Epoch 42/200"
)

This creates a `cryolo_model.h5` trained model file in the job directory.

## Picking

Use the trained model to predict particle locations for the full dataset.

In [27]:
output_folder = job_folder / "boxfiles"
output_folder.mkdir(exist_ok=True)

job.subprocess(
    ["cryolo_predict.py", "-c", "config_cryolo.json", "-w", "cryolo_model.h5"]
    + ["-i", full_data_folder.name, "-g", "0", "-o", output_folder.name, "-t", "0.3"],
    cwd=job_folder,
    mute=True,
    checkpoint=True,
)

For each micrograph in the full dataset, load the corresponding output particles star file, initialize a new empty particles dataset and fill in the predicted locations and other relevant location metadata.

Also fill in a dummy NCC score so that the results may be inspected with an Inspect Picks job.

In [28]:
output_star_folder = output_folder / "STAR"

all_predicted = []
for mic in all_micrographs.rows():
    micrograph_path = project_folder / mic["micrograph_blob/path"]
    height, width = mic["micrograph_blob/shape"]

    starfile_name = micrograph_path.stem + ".star"
    starfile_path = output_star_folder / starfile_name
    locations = star.read(starfile_path)[""]
    center_x = locations["rlnCoordinateX"] / width
    center_y = locations["rlnCoordinateY"] / height

    predicted = job.alloc_output("predicted_particles", len(locations))
    predicted["location/micrograph_uid"] = mic["uid"]
    predicted["location/micrograph_path"] = mic["micrograph_blob/path"]
    predicted["location/micrograph_shape"] = mic["micrograph_blob/shape"]
    predicted["location/center_x_frac"] = center_x
    predicted["location/center_y_frac"] = center_y
    predicted["pick_stats/ncc_score"] = 0.5

    all_predicted.append(predicted)

Output the most recent predicted particle locations to verify that crYOLO ran successfully.

In [30]:
header, mic = mrc.read(project_folder / micrograph_path)
binned = downsample(mic, factor=3)
lowpassed = lowpass(binned, psize_A=0.6575, cutoff_resolution_A=20, order=0.7)
height, width = lowpassed.shape
vmin = np.percentile(lowpassed, 1)
vmax = np.percentile(lowpassed, 99)

fig, ax = plt.subplots(figsize=(7.5, 8), dpi=144)
ax.axis("off")
ax.imshow(lowpassed, cmap="gray", vmin=vmin, vmax=vmax, origin="lower")
ax.scatter(center_x * width, center_y * height, c="cyan", marker="+")

fig.tight_layout()

Append all the predicted particles into a single dataset. Save this to the job and mark as completed.

In [31]:
from cryosparc.dataset import Dataset

job.save_output("predicted_particles", Dataset.append(*all_predicted))
job.stop()